# G10 Q1 Customer Booking ETL Process
### Created by: Ruhan Ahmed
### Created on: 01/07/2025
### Last updated by: Ruhan Ahmed
### Last updated on: 05/07/2025

# Extracting: 
### The data has been exported using Adobe Acrobat Pro text form features into multiple sheets

In [59]:
# Welcome to your new notebook
# Type here in the cell editor to add code!

import pandas as pd

# Helper to load and combine all sheets in a file
def load_and_combine_excel(file_path: str) -> pd.DataFrame:
    """
    Reads all sheets from an Excel file
    and concatenates them into a single DataFrame.

    :param file_path: the path to the Excel file.
    :return: the combined DataFrame.
    """

    xls = pd.ExcelFile(file_path)
    sheet_dfs = [xls.parse(sheet) for sheet in xls.sheet_names]
    return pd.concat(sheet_dfs, ignore_index=True)

# Base Lakehouse path (without the file name)
LAKEHOUSE = "abfss://fcadf7d8-0448-4cbc-a324-f9d13c00817d@onelake.dfs.fabric.microsoft.com/472b431a-5c41-4e10-994e-6ba64c998caa/Files/"

# Define paths for each file inside Lakehouse Files
jan_path = LAKEHOUSE + "01 - January pdf orders.xlsx"
feb_path = LAKEHOUSE + "02 - February pdf orders.xlsx"
mar_path = LAKEHOUSE + "03 - March pdf orders.xlsx"

# Load and combine each month's sheets
jan_df = load_and_combine_excel(jan_path)
feb_df = load_and_combine_excel(feb_path)
mar_df = load_and_combine_excel(mar_path)

# Combine all months into one DataFrame
q1_orders_df = pd.concat([jan_df, feb_df, mar_df], ignore_index=True)


# Preview the data
display(q1_orders_df)


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 60, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 298e4e2e-cb04-4e1c-a2df-25c8101966ae)

# Transform:
### Renaming & Dropping columns

In [60]:
def clean_orders(df: pd.DataFrame) -> pd.DataFrame:
    """
    Cleans the raw orders DataFrame by:
    - Renaming columns
    - Converting data types
    - Handling missing values

    :param df: The dataframe to be cleaned
    :return: The cleaned dataframe
    """

    # Rename relevant columns
    rename_map: dict[str, str] = {
        "Unnamed: 0": "source_file",
        "Text Field 63": "order_date",
        "Text Field 65": "date_required",
        "Text Field 64": "booking_number",
        "Text Field 66": "invoice_number",
        "Text Field 60": "production_order_number",
        "Text Field 61": "despatch_date",
        "Text Field 62": "despatch_number",
        "Text Field 118": "company_name",
        "Text Field 130": "ordered_by",
        "Text Field 180": "contact_number",
        "Text Field 178": "customer_order_number",

        # Booking data columns
        "Text Field 71": "quantity_field_1",
        "Text Field 135": "size_field_1",
        "Text Field 141": "paper_field_1",
        "Text Field 90": "description_field_1",
        "Text Field 102": "zero_rated_field_1",
        "Text Field 1010": "taxable_field_1",

        "Text Field 78": "quantity_field_2",
        "Text Field 136": "size_field_2",
        "Text Field 142": "paper_field_2",
        "Text Field 91": "description_field_2",
        "Text Field 103": "zero_rated_field_2",
        "Text Field 1011": "taxable_field_2",

        "Text Field 79": "quantity_field_3",
        "Text Field 137": "size_field_3",
        "Text Field 143": "paper_field_3",
        "Text Field 92": "description_field_3",
        "Text Field 104": "zero_rated_field_3",
        "Text Field 1012": "taxable_field_3",

        "Text Field 80": "quantity_field_4",
        "Text Field 138": "size_field_4",
        "Text Field 144": "paper_field_4",
        "Text Field 93": "description_field_4",
        "Text Field 105": "zero_rated_field_4",
        "Text Field 1013": "taxable_field_4",

        "Text Field 134": "special_info_field_1",
        "Text Field 179": "special_info_field_2",

        # Delivery data columns
        "Text Field 37": "delivery_contact",
        "Text Field 131": "delivery_mobile_number",
        "Text Field 132": "delivery_email",
        "Text Field 38": "delivery_address",
        "Text Field 133": "delivery_instructions"
    }
    
    df = df.rename(columns=rename_map)

    # Drop unused columns because it's empty boxes to be handwritten for printers downstairs
    # Also cost columns because I have the sales dataset which is more accurate
    df.drop(columns=[
        "production_order_number",
        "despatch_date",
        "despatch_number",
        "customer_order_number",
        "invoice_number",
        "zero_rated_field_1", "zero_rated_field_2", "zero_rated_field_3", "zero_rated_field_4",
        "taxable_field_1", "taxable_field_2", "taxable_field_3", "taxable_field_4",
        "special_info_field_1", "special_info_field_2"
    ], inplace=True, errors="ignore")

    # Drop completely empty rows
    df.dropna(how="all", inplace=True)

    # Reset index
    df = df.reset_index(drop=True)

    return df

df = clean_orders(q1_orders_df)

display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 61, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, f0143ed1-7bd9-410b-aaee-b864203517fc)

In [61]:
def parse_quantity(value: str | float) -> float | None:
    """
    Converts values like '2.5K' to 2500. Handles numbers, strings, and missing values.
    """

    if pd.isnull(value):
        return None
    
    try:
        # Convert to string and clean
        value_str = str(value).lower()
        
        # Remove common words/symbols
        for remove_str in ["copies", "'", ",", " ", "units", "quantity", "qty", ":", "-"]:
            value_str = value_str.replace(remove_str, "")
            
        value_str = value_str.strip()
        
        # Handle thousand indicators (k, thousand)
        if value_str.endswith("k"):
            return float(value_str[:-1]) * 1000
        elif value_str.endswith("thousand"):
            return float(value_str[:-8]) * 1000
    
        # Try direct conversion if no special suffixes
        return float(value_str)
        
    except (ValueError, AttributeError):
        return None

def convert_data_types(df):
    # Convert data types
    # type: float
    for quantity_field in ["quantity_field_1", "quantity_field_2", "quantity_field_3", "quantity_field_4"]:
        df[quantity_field] = df.get(quantity_field).apply(parse_quantity)

    # type: int
    for number in ["booking_number", "invoice_number"]:
        df[number] = pd.to_numeric(df[number], errors='coerce').astype('Int64')

    # Clean up client name and product type
    # type: str
    for name in ["ordered_by", "delivery_contact"]:
        df[name] = df.get(name, "").fillna("Unknown").astype(str).str.strip()

    return df

df = convert_data_types(df)

display(df)
print(df.dtypes)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 62, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 3af1638a-cda1-4d08-bfa6-2ef99e801749)

source_file                object
delivery_contact           object
delivery_address           object
order_date                 object
booking_number              Int64
date_required              object
invoice_number              Int64
quantity_field_1          float64
quantity_field_2          float64
quantity_field_3          float64
quantity_field_4          float64
description_field_1        object
description_field_2        object
description_field_3        object
description_field_4        object
company_name               object
ordered_by                 object
delivery_mobile_number     object
delivery_email             object
delivery_instructions      object
size_field_1               object
size_field_2               object
size_field_3               object
size_field_4               object
paper_field_1              object
paper_field_2              object
paper_field_3              object
paper_field_4              object
contact_number             object
dtype: object


In [62]:
def extract_from_source_file(df: pd.DataFrame) -> pd.DataFrame:
    """
    Splits 'source_file' into booking_number, company_name, and job_name.
    Replaces 'company_name' with the extracted version and validates consistency.
    
    :param df: Cleaned DataFrame with a 'source_file' column.
    :return: Updated DataFrame with separated and validated columns.
    """

    # Remove .pdf suffix and split by " - "
    split_cols = df["source_file"].str.replace(".pdf", "", regex=False).str.split(" - ", n=2, expand=True)
    df["booking_number_extracted"] = pd.to_numeric(split_cols[0], errors="coerce").astype('Int64')
    df["company_name"] = split_cols[1].str.strip().str.title()
    df["job_name"] = split_cols[2].str.strip().str.title()

    # Optional: Check for mismatch
    mismatches = df[df["booking_number_extracted"] != df["booking_number"]]
    if not mismatches.empty:
        print("⚠️ Warning: Booking number mismatch found in some rows.")
        display(mismatches[["source_file", "booking_number", "booking_number_extracted"]])

    # Drop original column
    df.drop(columns=["source_file"], inplace=True)

    return df

df = extract_from_source_file(df)
display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 63, Finished, Available, Finished)

⚠️ Warning: Booking number mismatch found in some rows.


SynapseWidget(Synapse.DataFrame, c5003e2d-3e2c-47ea-9a9d-d9f6ce2ee1cc)

SynapseWidget(Synapse.DataFrame, 2848a77e-b5ba-488f-a9c3-080ca596dc93)

In [63]:
# Replace incorrect booking numbers
df["booking_number"] = df["booking_number_extracted"]

# Drop the extracted column
df.drop(columns=["booking_number_extracted"], inplace=True)

display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 64, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, fe4706ca-c906-4c24-99e7-cc1b05bd6df6)

In [64]:
def reorder_columns(df: pd.DataFrame) -> pd.DataFrame:
    """
    Reorders the DataFrame columns in a specific layout:
    - booking_number, company_name, job_name, ordered_by, contact_number
    - Followed by booking fields in order (quantity, size, paper, description for each set)
    - Followed by any remaining columns

    :param df: The input DataFrame with cleaned and enriched data
    :return: A DataFrame with columns reordered according to the specified logic
    """

    # Desired initial columns
    main_columns = [
        "booking_number",
        "invoice_number",
        "company_name",     # from extracted data
        "job_name",         # from extracted data
        "order_date",
        "date_required",
        "ordered_by",
        "contact_number"
    ]

    # Define the desired column order
    booking_fields = []
    for i in range(1, 5):
        booking_fields.extend([
            f"quantity_field_{i}",
            f"size_field_{i}",
            f"paper_field_{i}",
            f"description_field_{i}"
        ])

    # Combine all columns in order
    final_column_order = main_columns + booking_fields

    # Add any remaining columns not listed above
    remaining_columns = [col for col in df.columns if col not in final_column_order]
    final_column_order += remaining_columns

    # Reorder the DataFrame
    df = df[final_column_order]

    return df

df = reorder_columns(df)
display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 65, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 0a108880-236c-429f-8f77-55cb71248380)

# Transforming:
# booking_number

In [65]:
null_booking_num_check1 = df[df["booking_number"].isna()]
display(null_booking_num_check1)

duplicates_check1 = df[df["booking_number"].duplicated(keep=False)]
display(duplicates_check1)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 66, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 7e58c3e1-5608-471b-bc94-5988193fcbd2)

SynapseWidget(Synapse.DataFrame, 3b789615-9116-4f53-b17f-a0d53615a257)

In [66]:
# Drops missing values of booking_number
# And keeps the last row of the duplicate booking_number
def booking_number_clean(df):
    df = df[df["booking_number"].notna()].copy()
    df = df[~df.duplicated(subset="booking_number", keep="last")]


    return df

df = booking_number_clean(df)

display(df)

null_booking_check2 = df[df["booking_number"].isna()]
display(null_booking_check2)

duplicates_check2 = df[df["booking_number"].duplicated(keep=False)]
display(duplicates_check2)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 67, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, e62e17eb-4997-444f-99c7-2f25b9581bd7)

SynapseWidget(Synapse.DataFrame, f8640d1a-33e0-476f-b71c-6d662ecb7f26)

SynapseWidget(Synapse.DataFrame, 187f0a93-2143-45df-b7ce-bff3d479edc5)

# Transforming:
# company_name, job_name

In [67]:
null_job_name_check1 = df[df["job_name"].isna()]
display(null_job_name_check1)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 68, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 88295beb-d51c-4e5f-89fd-5f104092f5ca)

In [68]:
# Manually changing
def company_job_clean(df):
    updates = {
        2501006: ("Ahead Design", "Spicy King"),
        2501010: ("One Step", "Golden Dragon"),
        2502416: ("We Design", "Lotus House"),
        2502424: ("We Design", "Top Chef"),
        2502583: ("We Design", "China King"),
        2502584: ("We Design", "China Rose"),
        2502588: ("We Design", "Happy Gourmet"),
        2502589: ("We Design", "Lams Kitchen"),
        2503415: ("We Design", "China Hall"),
        2503502: ("We Design", "The Bear Inn"),
    }

    for booking, (company, job) in updates.items():
        df.loc[df["booking_number"] == booking, "company_name"] = company
        df.loc[df["booking_number"] == booking, "job_name"] = job

    return df

df = company_job_clean(df)

null_job_name_check2 = df[df["job_name"].isna()]
display(null_job_name_check2)

display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 69, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 0bf0f050-632b-4938-9e94-6fe865a779e1)

SynapseWidget(Synapse.DataFrame, e758dbd6-2de0-47f2-b802-a3144038941f)

In [69]:
unique= df["company_name"].unique()

display(pd.DataFrame(sorted(unique), columns=["Unique Company Names"]))

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 70, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 9086a9ea-bd50-4a58-9eb6-c1e1b5cf577d)

In [70]:
# Mapping dictionary keys are now Title Case
company_relabel_map = {
    "16 Print": "16 Printing",
    "A&D Print": "A&D Printing",
    "Amaze Media": "Amaze Media Pro",
    "Aston Design": "Aston Design & Print",
    "Aston Print": "Aston Design & Print",
    "B1 Group": "B1 Media",
    "Bdsigns": "Bd Signs",
    "D&A Print": "D&A Printing",
    "Da Print": "Da Print Ltd",
    "Ema": "Ema Embroidery",
    "Impress": "Impress Media Uk",
    "Impress Media": "Impress Media Uk",
    "Inspire": "Inspire Print Ltd",
    "Inspire Print": "Inspire Print Ltd",
    "Jnb": "Jnb Prints",
    "Kabir Design": "Kabir Design & Print",
    "Menu Lane": "Menulane",
    "Metro Printers": "Metro Print",
    "Pixels Design": "Pixels Design Studio",
    "Premier Links": "Premier Linkz",
    "Print Today": "Print Today Uk",
    "Sign Genious": "Sign Genius",
    "Simply Menus": "Simply Menus Ltd",
    "Ultimate": "Ultimate Print & Design",
    "Ultimate Print": "Ultimate Print & Design",
    "Wang": "Wangland",
    "Wedesign": "We Design"
}

def relabel_company(name: str) -> str:
    if not isinstance(name, str):
        return name
    name_title = name.title().strip()
    # Lookup in title case keys
    new_name = company_relabel_map.get(name_title, name_title)
    return new_name

df["company_name"] = df["company_name"].apply(relabel_company)

unique = df["company_name"].unique()
display(pd.DataFrame(sorted(unique), columns=["Unique Company Names"]))


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 71, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, aa7c3e2a-b1f9-47be-981d-b2edb56fcb87)

# Transforming:
# order_date, date_required

In [71]:
import pandas as pd
import numpy as np
import re
from datetime import timedelta

def clean_dates_with_ranges(df: pd.DataFrame) -> pd.DataFrame:
    def parse_date_required(val, order_date):
        if pd.isnull(val):
            return np.nan

        # Case 1: Already a valid date
        try:
            parsed = pd.to_datetime(val, errors='coerce', dayfirst=True)
            if pd.notnull(parsed):
                return parsed
        except:
            pass

        # Case 2: Unix timestamp
        try:
            val_float = float(val)
            if val_float > 1e12:
                return pd.to_datetime(val_float, unit='ms')
        except:
            pass

        # Case 3: String like '1-3 days', '4-7 days urgent'
        if isinstance(val, str) and isinstance(order_date, pd.Timestamp):
            match = re.findall(r'\d+', val)
            if match:
                max_days = max(map(int, match))
                return order_date + timedelta(days=max_days)

        return np.nan

    # Ensure order_date is parsed correctly first
    df["order_date"] = pd.to_datetime(df["order_date"], errors="coerce", dayfirst=True)

    # Now clean date_required based on order_date
    df["date_required"] = df.apply(
        lambda row: parse_date_required(row["date_required"], row["order_date"]),
        axis=1
    )

    return df


def fix_date(date):

    year = date.year
    month = date.month
    day = date.day

    if year == 2024:
        if month != 12:
            # Swap day and month and set year to 2025
            try:
                swapped = pd.Timestamp(year=2025, month=day, day=month)
                if swapped.month in [1, 2, 3]:
                    return swapped
            except ValueError:
                # Invalid swapped date, keep original
                return date
    elif year == 2025:
        if month not in [1, 2, 3]:
            # Swap day and month keeping year 2025
            try:
                swapped = pd.Timestamp(year=2025, month=day, day=month)
                if swapped.month in [1, 2, 3]:
                    return swapped
            except ValueError:
                return date
    return date

df = clean_dates_with_ranges(df)

df['order_date'] = df['order_date'].apply(fix_date)
display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 72, Finished, Available, Finished)

/tmp/ipykernel_6014/701972201.py:13: UserWarning: Parsing dates in %m-%d-%Y format when dayfirst=True was specified. Pass `dayfirst=False` or specify a format to silence this warning.
  parsed = pd.to_datetime(val, errors='coerce', dayfirst=True)


SynapseWidget(Synapse.DataFrame, 99ddf20c-f662-490d-9d95-5696a806dafe)

In [72]:
# Filter rows where order_date year is 2024
orders_2024 = df[df['order_date'].dt.year == 2024]

display(orders_2024)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 73, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 30cfb5e2-7777-476d-b701-fd7ece4babc6)

In [73]:
invalid_2024 = df[(df['order_date'].dt.year == 2024) & (df["order_date"].dt.month != 12)]

display(invalid_2024)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 74, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 16e18b8b-bd40-43d7-92a4-170ec71e54b2)

In [74]:
# For 2024 dates that are not in December, change year to 2025
mask = (df['order_date'].dt.year == 2024) & (df['order_date'].dt.month != 12)

# Use apply with a function to update the year
df.loc[mask, 'order_date'] = df.loc[mask, 'order_date'].apply(
    lambda d: d.replace(year=2025)
)

# Convert order_date to datetime if it's not already
df['order_date'] = pd.to_datetime(df['order_date'], errors='coerce')

# Replace the specific date for 2502571
# Having checked the invoice data and using context
df.loc[df['order_date'] == pd.Timestamp('2025-04-26'), 'order_date'] = pd.Timestamp('2025-02-26')

invalid_2024_check = df[(df['order_date'].dt.year == 2024) & (df["order_date"].dt.month != 12)]

display(invalid_2024_check)

# Checking row to see if the date has been correctly applied
display(df[df['booking_number'] == 2502571])

# Set date_required to NaT if it's not after order_date
df.loc[df['date_required'] <= df['order_date'], 'date_required'] = pd.NaT


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 75, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 87236487-0717-47a4-9da4-acb2350cdf5a)

SynapseWidget(Synapse.DataFrame, 969370f1-68b1-4e38-99d9-a106290e2f29)

In [75]:
display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 76, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 0b39b27d-64f0-4911-861f-4714a841fe6a)

# Transformation:
# ordered_by, delivery_contact

In [76]:
columns_to_title = ['ordered_by', 'delivery_contact']

for col in columns_to_title:
    df[col] = df[col].apply(lambda x: x.title() if isinstance(x, str) else x)
    
display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 77, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 2b05d9f7-b3c6-4460-a0e3-cb103af6e15b)

# Transformation:
# size_fields

In [77]:
size_fields = ['size_field_1', 'size_field_2', 'size_field_3', 'size_field_4']

# Check if any of these columns contain 'A4' anywhere in the string
mask = df[size_fields].apply(lambda col: col.str.contains('A4', na=False))

# Keep rows where any column contains 'A4'
filtered_df = df[mask.any(axis=1)]

display(filtered_df)
print(filtered_df.dtypes)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 78, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 398f795c-2a30-4137-adfe-7cf028d84920)

booking_number                     Int64
invoice_number                     Int64
company_name                      object
job_name                          object
order_date                datetime64[ns]
date_required             datetime64[ns]
ordered_by                        object
contact_number                    object
quantity_field_1                 float64
size_field_1                      object
paper_field_1                     object
description_field_1               object
quantity_field_2                 float64
size_field_2                      object
paper_field_2                     object
description_field_2               object
quantity_field_3                 float64
size_field_3                      object
paper_field_3                     object
description_field_3               object
quantity_field_4                 float64
size_field_4                      object
paper_field_4                     object
description_field_4               object
delivery_contact

In [78]:
import re

def relabel_sizes(value: str | float | None) -> str | float | None:
    """
    Normalize and relabel paper size strings into standardized labels.

    This function processes an input value representing paper size descriptions,
    normalizes whitespace and case, and then applies pattern matching 
    to classify and relabel sizes consistently.

    Relabeling rules:

    - 'A4+', 'A4 plus' → 'A4+'
    - 'A4' → 'A4'
    - 'A3L', 'A3 long', 'long A3' → 'SRA3'
    - 'A3' → 'A3'
    - 'A2' → 'A2'
    - 'A1' → 'A1'
    - 'A0' → 'A0'
    - 'A5' with '6pp' → 'A5 6pp'
    - 'A5' without '6pp' → 'A5'
    - 'A6' → 'A6'
    - 'A7' → 'A7'
    - 'B4' → 'B4'
    - Contains 'bus' → 'Business Cards'
    - Contains 'ncr' → 'NCR Pads'
    - Contains 'dl' → 'DL'
    - Anything else → 'custom'

    :param value: Input value (string or NaN).
    :return: Standardized label or original value if NaN.
    """

    if value is None or (isinstance(value, float) and pd.isna(value)):
        return value

    val_norm = re.sub(r'\s+', ' ', str(value).lower()).strip()

    if re.search(r'a4\+|a4 plus', val_norm):
        return 'A4+'
    if re.search(r'\ba4\b', val_norm):
        return 'A4'
    if re.search(r'\b(a3l|a3 long|long a3)\b', val_norm):
        return 'SRA3'
    if re.search(r'\ba3\b', val_norm):
        return 'A3'
    if re.search(r'\ba2\b', val_norm):
        return 'A2'
    if re.search(r'\ba1\b', val_norm):
        return 'A1'
    if re.search(r'\ba0\b', val_norm):
        return 'A0'
    if re.search(r'\ba5\b', val_norm):
        if '6pp' in val_norm:
            return 'A5 6pp'
        else:
            return 'A5'
    if re.search(r'\ba6\b', val_norm):
        return 'A6'
    if re.search(r'\ba7\b', val_norm):
        return 'A7'
    if re.search(r'\bb4\b', val_norm):
        return 'B4'
    if 'bus' in val_norm:
        return 'Business Cards'
    if 'dl' or 'ncr' in val_norm:
        return 'DL'

    # Anything else
    return 'custom'

for column in size_fields:
    df[column] = df[column].apply(relabel_sizes)

display(df)


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 79, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, a021bae1-fa86-417c-88ef-74dd930d0757)

# Transformation:
# paper_field_1

In [79]:
# Count of nulls in paper_field_1
null_count = df['paper_field_1'].isnull().sum()
print(f"Number of null values in paper_field_1: {null_count}")

# Display rows where paper_field_1 is null
null_paper_check1 = df[df['paper_field_1'].isnull()]
display(null_paper_check1)


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 80, Finished, Available, Finished)

Number of null values in paper_field_1: 10


SynapseWidget(Synapse.DataFrame, 44476c20-1698-41a2-b57a-6382ac20d56f)

In [80]:
df['paper_field_1'] = df['paper_field_1'].fillna('banner/poster')

null_paper_check2 = df[df['paper_field_1'].isnull()]
display(null_paper_check2)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 81, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 0187e6b0-45a4-4312-8a96-32d71684379c)

In [81]:
def normalize_gsm(value: str | float | None) -> str | float | None:
    """
    Normalize paper weight strings by extracting the first number and appending 'gsm'.

    If the input is a string containing a number (e.g., '130gsm', '150gloss', '170gsm Silk'),
    this function extracts the first number and returns it followed by 'gsm' (e.g., '130gsm').

    If the input is not a string or does not contain any numbers, the original value is returned unchanged.

    :param value: The input value to normalize, typically a string or possibly NaN/None.
    :return: The normalized gsm string or the original value if no number is found or input is not string.
    """

    if not isinstance(value, str):
        return value
    
    # Search for the first number in the string
    match = re.search(r'(\d+)', value)
    if match:
        return f"{match.group(1)}gsm"
    else:
        return value

paper_fields = ['paper_field_1', 'paper_field_2', 'paper_field_3', 'paper_field_4']

for col in paper_fields:
    df[col] = df[col].apply(normalize_gsm)

display(df)


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 82, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 1423f7bc-1d4d-4048-b6e0-7b63be9b1353)

# Transformation:
# delivery_address

In [82]:
df.loc[df['delivery_address'].str.lower().str.contains('pick up|collection', na=False), 'delivery_address'] = 'Collection'

display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 83, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 6eb22aea-586b-4946-b37d-0f123be709aa)

In [83]:
import re

postcode_col = 'delivery_address'

# Updated UK postcode pattern allowing optional trailing comma/period/space
uk_postcode_pattern = r'(GIR 0AA|[A-Z]{1,2}\d{1,2} ?\d[ABD-HJLNP-UW-Z]{2}|[A-Z]{1,2}\d[A-Z] ?\d[ABD-HJLNP-UW-Z]{2})[,.\s]*$'

def has_valid_postcode(address: str) -> bool:
    if not isinstance(address, str):
        return False
    address_upper = address.upper().strip()
    # Check if postcode occurs near the end allowing trailing punctuation
    return bool(re.search(uk_postcode_pattern, address_upper))

valid_postcode_mask = df[postcode_col].apply(has_valid_postcode)

invalid_postcode_rows = df[~valid_postcode_mask]

display(invalid_postcode_rows)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 84, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 75552ca0-ae2c-44da-9aff-fb371ffced26)

In [84]:
# Dictionary of patterns and their replacements
address_replacements = {
    "Ultimate Print Office": "Ossington Rd, Kneesall, Newark NG22 0AB",
    "address": "Menu Address",
    "menu": "Menu Address",
    "us": "Company Address"
}

# Apply replacements
for keyword, replacement in address_replacements.items():
    df.loc[df['delivery_address'].str.contains(keyword, case=False, na=False), 'delivery_address'] = replacement


display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 85, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 1463af2d-3ad6-493c-a62c-538c51a5604f)

# Transformation: 
# contact_number, delivery_mobile_number

In [85]:
def clean_phone_number(number: str) -> str:
    """
    Cleans UK phone numbers by replacing '+44' with '0', removing non-digits,
    and adding a space after the first 5 digits.

    :param number: Original phone number string
    :return: Cleaned phone number in the format '07986 123456'
    """

    if not isinstance(number, str):
        return number

    # Replace +44 with 0
    number = number.replace('+44', '0')

    # Remove all non-digit characters
    digits = re.sub(r'\D', '', number)

    # Format with space after 5 digits if long enough
    if len(digits) > 5:
        cleaned = f"{digits[:5]} {digits[5:]}"
    else:
        cleaned = digits

    # Truncate to max 12 characters to avoid multiple numbers stuck together
    # Only gets the first number
    return str(cleaned[:12])

# Apply to both columns

for mobile_number in ["contact_number", "delivery_mobile_number"]:
    df[mobile_number] = df[mobile_number].apply(clean_phone_number)

display(df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 86, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, a958980e-0672-47b4-b9ca-d115f2386f91)

In [86]:
for col in df.columns:
    print(f"Column: {col}, unique types: ", df[col].map(type).unique())

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 87, Finished, Available, Finished)

Column: booking_number, unique types:  [<class 'int'>]
Column: invoice_number, unique types:  [<class 'pandas._libs.missing.NAType'> <class 'int'>]
Column: company_name, unique types:  [<class 'str'>]
Column: job_name, unique types:  [<class 'str'>]
Column: order_date, unique types:  [<class 'pandas._libs.tslibs.timestamps.Timestamp'>
 <class 'pandas._libs.tslibs.nattype.NaTType'>]
Column: date_required, unique types:  [<class 'pandas._libs.tslibs.nattype.NaTType'>
 <class 'pandas._libs.tslibs.timestamps.Timestamp'>]
Column: ordered_by, unique types:  [<class 'str'>]
Column: contact_number, unique types:  [<class 'float'> <class 'str'>]
Column: quantity_field_1, unique types:  [<class 'float'>]
Column: size_field_1, unique types:  [<class 'str'> <class 'float'>]
Column: paper_field_1, unique types:  [<class 'str'> <class 'int'>]
Column: description_field_1, unique types:  [<class 'str'> <class 'datetime.datetime'> <class 'float'>]
Column: quantity_field_2, unique types:  [<class 'float

In [87]:
# List of columns with mixed types
mixed_type_cols = [
    'contact_number', 'size_field_1', 'paper_field_1', 'description_field_1',
    'size_field_2', 'paper_field_2', 'description_field_2',
    'size_field_3', 'paper_field_3', 'description_field_3',
    'size_field_4', 'paper_field_4', 'description_field_4',
    'delivery_address', 'delivery_mobile_number', 'delivery_email',
    'delivery_instructions',
]

# Convert all mixed-type columns to string (handle NaNs properly)
for col in mixed_type_cols:
    df[col] = df[col].astype(str).replace('nan', None)

for col in df.columns:
    print(col)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 88, Finished, Available, Finished)

booking_number
invoice_number
company_name
job_name
order_date
date_required
ordered_by
contact_number
quantity_field_1
size_field_1
paper_field_1
description_field_1
quantity_field_2
size_field_2
paper_field_2
description_field_2
quantity_field_3
size_field_3
paper_field_3
description_field_3
quantity_field_4
size_field_4
paper_field_4
description_field_4
delivery_contact
delivery_address
delivery_mobile_number
delivery_email
delivery_instructions


# Transforming:
### Normalising database to 3NF
### Sales

In [88]:
import pandas as pd

# Load Excel
sales_df = pd.read_excel(LAKEHOUSE + "SALES DATA.xlsx")

# Keep only necessary columns
sales_df = sales_df[["No.", "Date", "Amount", "Sales Order No"]]

# Rename for consistency
sales_df.columns = ["invoice_number", "invoice_date", "amount", "booking_number"]

# Change invoice_date to date time
sales_df["invoice_date"] = pd.to_datetime(sales_df["invoice_date"], errors="coerce", dayfirst=True)

display(sales_df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 89, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 777aa238-a854-4a3b-9400-49ea44d68a78)

### Customers

In [89]:
# 1. Extract unique customers from df
customers_df = df[["company_name", "contact_number"]].drop_duplicates().reset_index(drop=True)

# 2. Assign a customer_id
customers_df["customer_id"] = customers_df.index + 1

# 3. Merge customer_id back into df so we can use it downstream
df = df.merge(customers_df, on=["company_name", "contact_number"], how="left")

display(customers_df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 90, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 2da9db9d-c5ec-46e1-8cb2-0c0c4b0c5630)

### Bookings

In [90]:
bookings_df = df[[
    "booking_number",
    "job_name",
    "order_date",
    "date_required",
    "customer_id"
]].drop_duplicates()

display(bookings_df)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 91, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 172c6000-da3a-4c29-9e33-e7e46f267a0e)

### Items

In [91]:
# Start by creating a list to store each item
items = []

# Go through each row in df
for _, row in df.iterrows():
    booking_number = row["booking_number"]
    
    # We expect up to 4 item fields per booking
    for i in range(1, 5):
        quantity = row.get(f"quantity_field_{i}")
        size = row.get(f"size_field_{i}")
        paper = row.get(f"paper_field_{i}")
        description = row.get(f"description_field_{i}")
        
        # Skip empty items (you can adjust this logic if needed)
        if pd.notna(quantity) or pd.notna(size) or pd.notna(paper) or pd.notna(description):
            items.append({
                "booking_number": booking_number,
                "item_number": i,
                "quantity": quantity,
                "size": size,
                "paper": paper,
                "description": description
            })

# Create the normalized item table
# And drops the null-quantity values
items_df = pd.DataFrame(items).dropna(subset=["quantity"])

display(items_df)
display(bookings_df)
display(customers_df)
display(sales_df)


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 92, Finished, Available, Finished)

SynapseWidget(Synapse.DataFrame, 94df9fc3-4937-4352-9f18-99daedc08d8f)

SynapseWidget(Synapse.DataFrame, 9ae53f0e-f86c-42b9-adbe-12b851ab6ee6)

SynapseWidget(Synapse.DataFrame, 8db6b398-b8c5-4465-82ff-60fc7b866515)

SynapseWidget(Synapse.DataFrame, 97da2f98-8993-48e0-bb1c-b58dd8cd1673)

In [92]:
for types in [items_df, bookings_df, customers_df, sales_df]:
    print(types.dtypes)

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 93, Finished, Available, Finished)

booking_number      int64
item_number         int64
quantity          float64
size               object
paper              object
description        object
dtype: object
booking_number             Int64
job_name                  object
order_date        datetime64[ns]
date_required     datetime64[ns]
customer_id                int64
dtype: object
company_name      object
contact_number    object
customer_id        int64
dtype: object
invoice_number             int64
invoice_date      datetime64[ns]
amount                   float64
booking_number             int64
dtype: object


# Load:
### Converting to Spark dataframe
### to save as deltatable in the lakehouse

In [93]:
items_sdf = spark.createDataFrame(items_df).write.format("delta").saveAsTable("items")
bookings_sdf = spark.createDataFrame(bookings_df).write.format("delta").saveAsTable("bookings")
customers_sdf = spark.createDataFrame(customers_df).write.format("delta").saveAsTable("customers")
sales_sdf = spark.createDataFrame(sales_df).write.format("delta").saveAsTable("sales")

StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 94, Finished, Available, Finished)

# 1. Total Sales per Customer

In [94]:
%%sql
SELECT
  c.customer_id,
  c.company_name,
  SUM(s.amount) AS total_revenue
FROM customers c
JOIN bookings b ON c.customer_id = b.customer_id
JOIN sales s ON b.booking_number = s.booking_number
GROUP BY c.customer_id, c.company_name
ORDER BY total_revenue DESC;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 95, Finished, Available, Finished)

<Spark SQL result set with 111 rows and 3 fields>

# 2. Top 5 Customers by Revenue

In [95]:
%%sql
WITH cust_rev AS (
  SELECT b.customer_id, SUM(s.amount) AS revenue
  FROM bookings b
  JOIN sales s ON b.booking_number = s.booking_number
  GROUP BY b.customer_id
)
SELECT
  cr.customer_id,
  c.company_name,
  cr.revenue
FROM cust_rev cr
JOIN customers c ON cr.customer_id = c.customer_id
ORDER BY cr.revenue DESC
LIMIT 5;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 96, Finished, Available, Finished)

<Spark SQL result set with 5 rows and 3 fields>

# 3. Monthly Sales Trend

In [96]:
%%sql
SELECT
  DATE_TRUNC('month', s.invoice_date) AS month,
  SUM(s.amount) AS monthly_revenue
FROM sales s
GROUP BY 1
ORDER BY 1;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 97, Finished, Available, Finished)

<Spark SQL result set with 4 rows and 2 fields>

# 4. Average Invoice Amount by Month

In [97]:
%%sql
SELECT
  DATE_TRUNC('month', invoice_date) AS month,
  AVG(amount) AS avg_invoice_amt
FROM sales
GROUP BY 1
ORDER BY 1;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 98, Finished, Available, Finished)

<Spark SQL result set with 4 rows and 2 fields>

# 5. Total Quantity Sold by Size

In [98]:
%%sql
SELECT
  i.size,
  SUM(i.quantity) AS total_quantity
FROM items i
GROUP BY i.size
ORDER BY total_quantity DESC;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 99, Finished, Available, Finished)

<Spark SQL result set with 15 rows and 2 fields>

# 6. Revenue by Paper Type

In [99]:
%%sql
SELECT
  i.paper,
  SUM(s.amount) AS revenue
FROM items i
JOIN bookings b ON i.booking_number = b.booking_number
JOIN sales s ON b.booking_number = s.booking_number
GROUP BY i.paper
ORDER BY revenue DESC;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 100, Finished, Available, Finished)

<Spark SQL result set with 40 rows and 2 fields>

# 7. Average Lead Time (Order to Required Date)

In [100]:
%%sql
SELECT
  AVG(DATEDIFF(b.date_required, b.order_date)) AS avg_lead_days
FROM bookings b;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 101, Finished, Available, Finished)

<Spark SQL result set with 1 rows and 1 fields>

# 8. Items per Booking Distribution

In [101]:
%%sql
SELECT
  item_count,
  COUNT(*) AS num_bookings
FROM (
  SELECT booking_number, COUNT(*) AS item_count
  FROM items
  GROUP BY booking_number
) t
GROUP BY item_count
ORDER BY item_count;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 102, Finished, Available, Finished)

<Spark SQL result set with 4 rows and 2 fields>

# 9. Bookings without any Sales (Unbilled Orders)

In [102]:
%%sql
SELECT
  b.booking_number,
  b.job_name,
  b.order_date
FROM bookings b
LEFT JOIN sales s ON b.booking_number = s.booking_number
WHERE s.booking_number IS NULL;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 103, Finished, Available, Finished)

<Spark SQL result set with 700 rows and 3 fields>

# 10. Backlog Orders (Required Date After Today)

In [103]:
%%sql
SELECT
  b.booking_number,
  b.job_name,
  b.date_required,
  DATEDIFF(b.date_required, CURRENT_DATE()) AS days_until_due
FROM bookings b
WHERE b.date_required > CURRENT_DATE()
ORDER BY days_until_due;


StatementMeta(, f32ef085-a6bd-41e5-801e-97c41e80b1cf, 104, Finished, Available, Finished)

<Spark SQL result set with 20 rows and 4 fields>